In [168]:
# Dependancies 
import requests
import random
import json
import urllib.parse
import time
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from pprint import pprint
from scipy.stats import zscore
from datetime import datetime

In [2]:
api_key = "f1a394a4c08c86f2a95946f07a41cad7"
headers = {"apikey": api_key}

In [3]:
# Austin metropolitan area ZipCodes
postal_codes = [
    "78613", "78617", "78620", "78628", "78641", "78645", "78652",
    "78701", "78702", "78703", "78704", "78705", "78717", "78721",
    "78722", "78723", "78724", "78726", "78728", "78731", "78732",
    "78733", "78734", "78735", "78737", "78738", "78739", "78741",
    "78744", "78745", "78748", "78749", "78750", "78751", "78752",
    "78753", "78754", "78756", "78757", "78758"
]

In [9]:
# Collect the addresses
selected_data = []

for post in postal_codes:
    page = 1  
    url_template = f"https://api.gateway.attomdata.com/propertyapi/v1.0.0/property/expandedprofile?postalcode={post}&page={{page}}&pagesize=5000"

    while True:
        time.sleep(5)
        response = requests.get(url_template.format(page=page), headers=headers)

        if response.status_code == 200:
            data = response.json()

            # Extract the specific keys
            if data.get('property', []):
                for prop in data['property']:
                    # Extract sale information
                    sale_info = prop.get('sale', {})
                    sale_amt = sale_info.get('amount', {}).get('saleAmt', 0)
                    sale_trans_date = sale_info.get('saleTransDate', '')

                    address_data = {
                        'address': prop['address'].get('line1', ''),
                        'city': prop['address'].get('locality', ''),
                        'state': prop['address'].get('countrySubd', ''),
                        'latitude': prop['location'].get('latitude', ''),
                        'longitude': prop['location'].get('longitude', ''),
                        'bedrooms': prop['building']['rooms'].get('beds', 0),
                        'bathrooms': prop['building']['rooms'].get('bathsTotal', 0),
                        'property_size (sqr ft)': prop['building']['size'].get('grossSize', 0),
                        'property_class': prop['summary'].get('propClass', ''),
                        'price': prop['assessment']['market'].get('mktTtlValue', 0),
                        'zipcode': prop['address'].get('postal1', ''),
                        'sale_amount': sale_amt,
                        'sale_transaction_date': sale_trans_date
                    }
                    
                    # Conditionals 
                    if all(
                        address_data[key] > 0
                        and (key != 'address' or address_data[key] != '')
                        for key in ['bedrooms', 'bathrooms', 'property_size (sqr ft)', 'price']
                    ) and address_data['property_class'] in ["Single Family Residence / Townhouse", "Apartment", "Condominium"] and \
                            sale_amt > 0 and sale_trans_date >= '2020-01-01':
                        
                        selected_data.append(address_data)
                        
                page += 1
            else:
                break
        else:
            print(f"Error: {response.status_code}")
            break

pprint(selected_data)

Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
Error: 400
[{'address': '2704 ORSOBELLO PL',
  'bathrooms': 3.0,
  'bedrooms': 4,
  'city': 'CEDAR PARK',
  'latitude': '30.463011',
  'longitude': '-97.846630',
  'price': 827510.0,
  'property_class': 'Single Family Residence / Townhouse',
  'property_size (sqr ft)': 3715.0,
  'sale_amount': 503723.0,
  'sale_transaction_date': '2020-01-30',
  'state': 'TX',
  'zipcode': '78613'},
 {'address': '2705 QUIET MOON TRL',
  'bathrooms': 4.0,
  'bedrooms': 5,
  'city': 'CEDAR PARK',
  'latitude': '30.473855',
  'longitude': '-97.853806',
  'price': 1064554.0,
  'propert

In [11]:
# Save addresses as json file
json_file_path = 'final_addresses.json'

with open(json_file_path, 'w') as json_file:
    json.dump(selected_data, json_file, indent=2) 

In [4]:
# Open the JSON file for reading
json_file_path = 'final_addresses.json'

with open(json_file_path, 'r') as file:
    selected_data = json.load(file)

In [6]:
# Save the unique Address and City combinations 
unique_data = []
unique_key_set = set()

for prop in selected_data:
    key = (prop['address'], prop['city'])

    if key not in unique_key_set:
        unique_key_set.add(key)
        unique_data.append(prop)

len(unique_data)

8882

In [7]:
# Save unique addresses as json file
json_file_path = 'unique_addresses.json'

with open(json_file_path, 'w') as json_file:
    json.dump(unique_data, json_file, indent=2) 

In [236]:
# START HERE IF DATA IS ALREADY POPULATED TO JSON
# --------------------------------------------------------------------------------------------------------
# Read in the DF
json_file_path = 'unique_addresses.json'

with open('unique_addresses.json', 'r') as file:
    unique_data = pd.read_json(file)

In [237]:
# Dataframe with ALL columns 
extra_df = pd.DataFrame(unique_data)

# Dataframe with limited columns
df = pd.DataFrame(unique_data)
df = df[['city', 'state', 'zipcode', 'address', 'price', 'bedrooms', 'bathrooms', 'property_size (sqr ft)', 'latitude', 'longitude', 'sale_amount', 'sale_transaction_date' ]]

In [238]:
# Rename Columns
df.rename(columns={'property_size (sqr ft)': 'square_foot'}, inplace=True)
df

city state  zipcode                 address    price  bedrooms  \
0     CEDAR PARK    TX    78613       2704 ORSOBELLO PL   827510         4   
1     CEDAR PARK    TX    78613     2705 QUIET MOON TRL  1064554         5   
2     CEDAR PARK    TX    78613      3204 APPENNINI WAY   956365         4   
3     CEDAR PARK    TX    78613      3125 FIORELLINO PL   776845         4   
4     CEDAR PARK    TX    78613        2316 ALDWORTH DR   945000         6   
...          ...   ...      ...                     ...      ...       ...   
8877      AUSTIN    TX    78758  1401 LORRAINE LOOP # B   485155         2   
8878      AUSTIN    TX    78758     1420A LORRAINE LOOP   449941         2   
8879      AUSTIN    TX    78758      1509 LORRAINE LOOP   541362         3   
8880      AUSTIN    TX    78758     1417 KRAMER LN # 10   701193         3   
8881      AUSTIN    TX    78758      1417 KRAMER LN # 8   701193         3   

      bathrooms  square_foot   latitude  longitude  sale_amount  \
0             3         3715  30.463011 -97.846630       503723   
1             4         5018  30.473855 -97.853806      1100000   
2             3         4145  30.456254 -97.849748       679630   
3             3         3624  30.454730 -97.848842       609375   
4             4         4725  30.467167 -97.851148       781250   
...         ...          ...        ...        ...          ...   
8877          2         1596  30.381360 -97.703334       475000   
8878          2         1596  30.381360 -97.703334       362188   
8879          3         1718  30.381360 -97.703334       540000   
8880          3         2428  30.383131 -97.699892       700000   
8881          3         2428  30.383131 -97.699892       385000   

     sale_transaction_date  
0               2020-01-30  
1               2022-03-25  
2               2020-09-10  
3               2023-01-04  
4               2021-12-13  
...                    ...  
8877            2021-08-24  
8878            2020-06-01  
8879            2022-05-06  
8880            2022-04-01  
8881            2020-10-14  

[8882 rows x 12 columns]

In [239]:
# Check for null values
null_values = df.isnull().sum()
print(null_values)

city                     0
state                    0
zipcode                  0
address                  0
price                    0
bedrooms                 0
bathrooms                0
square_foot              0
latitude                 0
longitude                0
sale_amount              0
sale_transaction_date    0
dtype: int64


In [240]:
# Checks for Nulls, 0s, and Placeholder Values in the data
for col in df.columns:
    if pd.api.types.is_numeric_dtype(df[col]):
        print(f"Number of 0 values in {col}: {len(df[df[col] == 0])}")
    if pd.api.types.is_string_dtype(df[col]):
        print(f"Number of empty strings in {col}: {len(df[df[col] == ''])}")
        placeholder_values = df[df[col].isin(['NA', 'N/A'])]
        print(f"Number of placeholder values in {col}: {len(placeholder_values)}")

Number of empty strings in city: 0
Number of placeholder values in city: 0
Number of empty strings in state: 0
Number of placeholder values in state: 0
Number of 0 values in zipcode: 0
Number of empty strings in address: 0
Number of placeholder values in address: 0
Number of 0 values in price: 0
Number of 0 values in bedrooms: 0
Number of 0 values in bathrooms: 0
Number of 0 values in square_foot: 0
Number of 0 values in latitude: 0
Number of 0 values in longitude: 0
Number of 0 values in sale_amount: 0
Number of empty strings in sale_transaction_date: 0
Number of placeholder values in sale_transaction_date: 0


In [241]:
df_outlier = df.copy()

# Convert 'sale_transaction_date' to datetime
df_outlier['sale_transaction_date'] = pd.to_datetime(df_outlier['sale_transaction_date'])

# Set the specific date for calculations (December 8th)
specific_date = pd.to_datetime('2023-12-08')

# Calculate the time difference in years
df_outlier['years_since_last_sale'] = (specific_date - df_outlier['sale_transaction_date']).dt.days / 365.25

# Calculate the yearly percentage price change (positive or negative)
df_outlier['yearly_price_change'] = (df_outlier['price'] - df_outlier['sale_amount']) / df_outlier['sale_amount'] * 100 / df_outlier['years_since_last_sale']

# Calculate the size/bedroom+bathroom ratio
df_outlier['size_bedroom_bathroom_ratio'] = df_outlier['square_foot'] / (df_outlier['bedrooms'] + df_outlier['bathrooms'])

# Display the DataFrame with new and original columns
df_outlier

city state  zipcode                 address    price  bedrooms  \
0     CEDAR PARK    TX    78613       2704 ORSOBELLO PL   827510         4   
1     CEDAR PARK    TX    78613     2705 QUIET MOON TRL  1064554         5   
2     CEDAR PARK    TX    78613      3204 APPENNINI WAY   956365         4   
3     CEDAR PARK    TX    78613      3125 FIORELLINO PL   776845         4   
4     CEDAR PARK    TX    78613        2316 ALDWORTH DR   945000         6   
...          ...   ...      ...                     ...      ...       ...   
8877      AUSTIN    TX    78758  1401 LORRAINE LOOP # B   485155         2   
8878      AUSTIN    TX    78758     1420A LORRAINE LOOP   449941         2   
8879      AUSTIN    TX    78758      1509 LORRAINE LOOP   541362         3   
8880      AUSTIN    TX    78758     1417 KRAMER LN # 10   701193         3   
8881      AUSTIN    TX    78758      1417 KRAMER LN # 8   701193         3   

      bathrooms  square_foot   latitude  longitude  sale_amount  \
0             3         3715  30.463011 -97.846630       503723   
1             4         5018  30.473855 -97.853806      1100000   
2             3         4145  30.456254 -97.849748       679630   
3             3         3624  30.454730 -97.848842       609375   
4             4         4725  30.467167 -97.851148       781250   
...         ...          ...        ...        ...          ...   
8877          2         1596  30.381360 -97.703334       475000   
8878          2         1596  30.381360 -97.703334       362188   
8879          3         1718  30.381360 -97.703334       540000   
8880          3         2428  30.383131 -97.699892       700000   
8881          3         2428  30.383131 -97.699892       385000   

     sale_transaction_date  years_since_last_sale  yearly_price_change  \
0               2020-01-30               3.854894            16.674591   
1               2022-03-25               1.705681            -1.889195   
2               2020-09-10               3.241615            12.561169   
3               2023-01-04               0.925394            29.697912   
4               2021-12-13               1.984942            10.559503   
...                    ...                    ...                  ...   
8877            2021-08-24               2.288843             0.934050   
8878            2020-06-01               3.518138             6.886761   
8879            2022-05-06               1.590691             0.158561   
8880            2022-04-01               1.686516             0.101054   
8881            2020-10-14               3.148528            26.084583   

      size_bedroom_bathroom_ratio  
0                      530.714286  
1                      557.555556  
2                      592.142857  
3                      517.714286  
4                      472.500000  
...                           ...  
8877                   399.000000  
8878                   399.000000  
8879                   286.333333  
8880                   404.666667  
8881                   404.666667  

[8882 rows x 15 columns]

In [242]:
# size_bedroom_bathroom ratio IQR calcuation
q1_size_ratio = df_outlier['size_bedroom_bathroom_ratio'].quantile(0.25)
q3_size_ratio = df_outlier['size_bedroom_bathroom_ratio'].quantile(0.75)
iqr_size_ratio = q3_size_ratio - q1_size_ratio

lower_bound_size_ratio = q1_size_ratio - 1.5 * iqr_size_ratio

outliers_size_ratio = df_outlier.loc[
    (df_outlier['size_bedroom_bathroom_ratio'] < lower_bound_size_ratio)]

print("Q1 for size_bedroom_bathroom_ratio:", q1_size_ratio)
print("Q3 for size_bedroom_bathroom_ratio:", q3_size_ratio)
print("IQR for size_bedroom_bathroom_ratio:", iqr_size_ratio)
outliers_size_ratio

Q1 for size_bedroom_bathroom_ratio: 367.0416666666667
Q3 for size_bedroom_bathroom_ratio: 539.3833333333333
IQR for size_bedroom_bathroom_ratio: 172.34166666666664


city state  zipcode                address    price  bedrooms  \
974   AUSTIN    TX    78702    2537 SOL WILSON AVE   300001         4   
984   AUSTIN    TX    78702         1606 HARVEY ST  1007947         3   
1064  AUSTIN    TX    78702      1611 CLIFFORD AVE   525280         3   
1144  AUSTIN    TX    78702      2106 RIVERVIEW ST  2035368         3   
1145  AUSTIN    TX    78702           73 JULIUS ST   931203         3   
1146  AUSTIN    TX    78702         1205 TAYLOR ST   382501         3   
1154  AUSTIN    TX    78702     2213 SANTA ROSA ST  1154360         4   
1165  AUSTIN    TX    78702    2731 WEBBERVILLE RD   950359         4   
1168  AUSTIN    TX    78702           800 MAUDE ST   446611         4   
1170  AUSTIN    TX    78702          3004 PRADO ST  1591736         3   
1181  AUSTIN    TX    78702        1301 WALNUT AVE   521272         4   
1204  AUSTIN    TX    78702          1507 E 2ND ST   450002         4   
1330  AUSTIN    TX    78703        1702 WINSTED LN  1500000         5   
1431  AUSTIN    TX    78703     1615 WATERSTON AVE  1237459         5   
1628  AUSTIN    TX    78704     2102 MONTCLAIRE ST  2683107         5   
1662  AUSTIN    TX    78704        2109 ARPDALE ST  2202788         4   
1670  AUSTIN    TX    78704        2012 OXFORD AVE  2009380         4   
1696  AUSTIN    TX    78704        3004 KINNEY AVE  1812935         4   
1729  AUSTIN    TX    78704         1503 DEXTER ST  2136792         5   
1747  AUSTIN    TX    78704          2602 S 3RD ST  2157788         3   
1822  AUSTIN    TX    78704        1811 KINNEY AVE  2196430         4   
1865  AUSTIN    TX    78705          3711 CEDAR ST  1225000         4   
2018  AUSTIN    TX    78721  3414 PENNSYLVANIA AVE   480087         4   
2036  AUSTIN    TX    78721  3602 PENNSYLVANIA AVE   985908         4   
2054  AUSTIN    TX    78721        1311 DELONEY ST   415344         3   
2056  AUSTIN    TX    78721          1801 PEREZ ST   334410         5   
2163  AUSTIN    TX    78722         2100 CHICON ST   875907         5   
3443  AUSTIN    TX    78731         1908 W 36TH ST  1416303         4   
4754  AUSTIN    TX    78737       160 MENDOCINO LN   881270         4   
6339  AUSTIN    TX    78741          712 VARGAS RD   452955         3   
6578  AUSTIN    TX    78745   4702 MOUNT VERNON DR  1398864         6   
6672  AUSTIN    TX    78745         401 N BLUFF DR   352375         3   
6675  AUSTIN    TX    78745      4616 RICHMOND AVE  1901986         4   
7523  AUSTIN    TX    78751          603 E 47TH ST   738442         4   
7552  AUSTIN    TX    78751        3912 BECKER AVE  1318840         4   
7562  AUSTIN    TX    78751          4608 AVENUE H   684497         4   
7717  AUSTIN    TX    78753          100 E HOME PL   260000         4   
8300  AUSTIN    TX    78756         1305 W 42ND ST  1453946         4   
8489  AUSTIN    TX    78757         1701 ALGUNO RD  1800000         4   
8503  AUSTIN    TX    78757        6601 GROVER AVE  1430038         5   
8561  AUSTIN    TX    78757       1913 MADISON AVE  2008061         4   

      bathrooms  square_foot   latitude  longitude  sale_amount  \
974           4          840  30.274646 -97.706339      1437500   
984           2          480  30.279683 -97.705452       406875   
1064          3          480  30.279738 -97.707029       826875   
1144          3          648  30.250836 -97.723818      1985000   
1145          3          576  30.251816 -97.717106       681563   
1146          2          489  30.256482 -97.733721       427000   
1154          3          504  30.258321 -97.718539      1104513   
1165          4          808  30.264317 -97.710716      1307500   
1168          4          744  30.262935 -97.709292      1218750   
1170          4          525  30.261344 -97.706255      1080000   
1181          3          672  30.276166 -97.712102       656250   
1204          4          713  30.259364 -97.728926       792188   
1330          4          952  30.289128 -97.762853      1306250   
143

In [243]:
# Capture visulization for demonstration
outliers_size_ratio[['square_foot', 'bedrooms', 'bathrooms']].head(5)

square_foot  bedrooms  bathrooms
974           840         4          4
984           480         3          2
1064          480         3          3
1144          648         3          3
1145          576         3          3

In [244]:
# Remove houses with a small SQFT to room ratio 
df_outlier = df_outlier[~(df_outlier['size_bedroom_bathroom_ratio'] < lower_bound_size_ratio)]
df_outlier

city state  zipcode                 address    price  bedrooms  \
0     CEDAR PARK    TX    78613       2704 ORSOBELLO PL   827510         4   
1     CEDAR PARK    TX    78613     2705 QUIET MOON TRL  1064554         5   
2     CEDAR PARK    TX    78613      3204 APPENNINI WAY   956365         4   
3     CEDAR PARK    TX    78613      3125 FIORELLINO PL   776845         4   
4     CEDAR PARK    TX    78613        2316 ALDWORTH DR   945000         6   
...          ...   ...      ...                     ...      ...       ...   
8877      AUSTIN    TX    78758  1401 LORRAINE LOOP # B   485155         2   
8878      AUSTIN    TX    78758     1420A LORRAINE LOOP   449941         2   
8879      AUSTIN    TX    78758      1509 LORRAINE LOOP   541362         3   
8880      AUSTIN    TX    78758     1417 KRAMER LN # 10   701193         3   
8881      AUSTIN    TX    78758      1417 KRAMER LN # 8   701193         3   

      bathrooms  square_foot   latitude  longitude  sale_amount  \
0             3         3715  30.463011 -97.846630       503723   
1             4         5018  30.473855 -97.853806      1100000   
2             3         4145  30.456254 -97.849748       679630   
3             3         3624  30.454730 -97.848842       609375   
4             4         4725  30.467167 -97.851148       781250   
...         ...          ...        ...        ...          ...   
8877          2         1596  30.381360 -97.703334       475000   
8878          2         1596  30.381360 -97.703334       362188   
8879          3         1718  30.381360 -97.703334       540000   
8880          3         2428  30.383131 -97.699892       700000   
8881          3         2428  30.383131 -97.699892       385000   

     sale_transaction_date  years_since_last_sale  yearly_price_change  \
0               2020-01-30               3.854894            16.674591   
1               2022-03-25               1.705681            -1.889195   
2               2020-09-10               3.241615            12.561169   
3               2023-01-04               0.925394            29.697912   
4               2021-12-13               1.984942            10.559503   
...                    ...                    ...                  ...   
8877            2021-08-24               2.288843             0.934050   
8878            2020-06-01               3.518138             6.886761   
8879            2022-05-06               1.590691             0.158561   
8880            2022-04-01               1.686516             0.101054   
8881            2020-10-14               3.148528            26.084583   

      size_bedroom_bathroom_ratio  
0                      530.714286  
1                      557.555556  
2                      592.142857  
3                      517.714286  
4                      472.500000  
...                           ...  
8877                   399.000000  
8878                   399.000000  
8879                   286.333333  
8880                   404.666667  
8881                   404.666667  

[8841 rows x 15 columns]

In [245]:
# yearly_priuce_change IQR calculation 
q1_price_change = df_outlier['yearly_price_change'].quantile(0.25)
q3_price_change = df_outlier['yearly_price_change'].quantile(0.75)
iqr_price_change = q3_price_change - q1_price_change

lower_bound_price_change = q1_price_change - 2 * iqr_price_change
upper_bound_price_change = q3_price_change + 2 * iqr_price_change

outliers_price_change = df_outlier[
    (df_outlier['yearly_price_change'] < lower_bound_price_change) |
    (df_outlier['yearly_price_change'] > upper_bound_price_change)
]

print("Q1 for yearly_price_change:", q1_price_change)
print("Q3 for yearly_price_change:", q3_price_change)
print("IQR for yearly_price_change:", iqr_price_change)
outliers_price_change

Q1 for yearly_price_change: -0.3295088795369559
Q3 for yearly_price_change: 20.04784142710095
IQR for yearly_price_change: 20.377350306637904


city state  zipcode                address   price  bedrooms  \
6     CEDAR PARK    TX    78613      1701 HONEYWEED ST  348687         3   
28    CEDAR PARK    TX    78613        2607 SALERNO PL  741046         4   
31    CEDAR PARK    TX    78613       1106 RED BIRD DR  459885         3   
33    CEDAR PARK    TX    78613     1500 SKIP TYLER DR  788946         4   
49    CEDAR PARK    TX    78613          2210 MACAW DR  499386         3   
...          ...   ...      ...                    ...     ...       ...   
8807      AUSTIN    TX    78758  1805 RAINY MEADOWS DR  488325         2   
8813      AUSTIN    TX    78758         1204 GEMINI DR  573847         3   
8832      AUSTIN    TX    78758      1205 FAIRFIELD DR  487098         3   
8852      AUSTIN    TX    78758   10409 QUAIL RIDGE DR  461996         3   
8875      AUSTIN    TX    78758     1400 LORRAINE LOOP  599107         3   

      bathrooms  square_foot   latitude  longitude  sale_amount  \
6             2         1712  30.464326 -97.830438       457875   
28            2         3764  30.461311 -97.847166         1250   
31            3         2175  30.468366 -97.822118       168750   
33            2         3356  30.480505 -97.852275       599872   
49            2         2327  30.465293 -97.841686       187500   
...         ...          ...        ...        ...          ...   
8807          2         1388  30.395860 -97.701543       362500   
8813          2         2488  30.387058 -97.692940       658125   
8832          2         1792  30.359446 -97.710482       365000   
8852          2         1917  30.380669 -97.705156       143750   
8875          2         1863  30.381360 -97.703334       407000   

     sale_transaction_date  years_since_last_sale  yearly_price_change  \
6               2023-06-22               0.462697           -51.538467   
28              2022-02-08               1.828884         32360.537605   
31              2022-05-10               1.579740           109.210664   
33              2023-06-30               0.440794            71.505191   
49              2021-12-22               1.960301            84.853901   
...                    ...                    ...                  ...   
8807            2023-06-23               0.459959            75.464009   
8813            2023-08-29               0.276523           -46.309990   
8832            2023-06-28               0.446270            74.958054   
8852            2021-12-23               1.957563           113.093927   
8875            2023-06-21               0.465435           101.412172   

      size_bedroom_bathroom_ratio  
6                      342.400000  
28                     627.333333  
31                     362.500000  
33                     559.333333  
49                     465.400000  
...                           ...  
8807                   347.000000  
8813                   497.600000  
8832                   358.400000  
8852                   383.400000  
8875                   372.600000  

[772 rows x 15 columns]

In [246]:
# Selecting the price change outliers
price_outliers = outliers_price_change.sort_values(by='yearly_price_change', ascending=False).head(30)
price_outliers

city state  zipcode                      address    price  \
4572            AUSTIN    TX    78735              4908 PERALTA LN  4833563   
28          CEDAR PARK    TX    78613              2607 SALERNO PL   741046   
4159            AUSTIN    TX    78734            3101 CHISHOLM TRL   450080   
3477            AUSTIN    TX    78731            7213 LAMPLIGHT LN  1897071   
6659            AUSTIN    TX    78745               7601 COOPER LN  6754950   
1556            AUSTIN    TX    78704             2006 DE VERNE ST  1050000   
1763            AUSTIN    TX    78704             1107 W MONROE ST  2164466   
5059            AUSTIN    TX    78738  5316 SPANISH OAKS CLUB BLVD  2674347   
3982            AUSTIN    TX    78734              4503 POTEAU CIR  1430258   
6978            AUSTIN    TX    78748       9613 SYDNEY MARILYN LN   466878   
8482            AUSTIN    TX    78757        7501 SAINT CECELIA ST   883774   
623         LAGO VISTA    TX    78645            21003 POST OAK DR   546823   
1498            AUSTIN    TX    78703               2103 QUARRY RD  1769443   
283   DRIPPING SPRINGS    TX    78620             6300 MCGREGOR LN  1550000   
4474            AUSTIN    TX    78735         5701 JOURNEYVILLE CT   942984   
2344            AUSTIN    TX    78723        2024 SIMOND AVE APT A   220000   
5408            AUSTIN    TX    78738          12217 IRON BLUFF PL  3827414   
160          DEL VALLE    TX    78617                8421 ELROY RD   389673   
8436            AUSTIN    TX    78757               1807 KENDRA CV   535171   
4493            AUSTIN    TX    78735      4020 TEXAS WILDLIFE TRL  2001032   
1809            AUSTIN    TX    78704            1106 SOUTHWOOD RD  1227759   
8606            AUSTIN    TX    78757              1000 ALEGRIA RD   512552   
702         LAGO VISTA    TX    78645             204 CHAMPIONS CV   519955   
3718            AUSTIN    TX    78732    12713 MONTE CASTILLO PKWY  1450763   
5283           LAKEWAY    TX    78738          211 GRANT CANNON LN   936608   
2339            AUSTIN    TX    78723               2221 ANTONE ST   682057   
835           MANCHACA    TX    78652            11228 ASHBROOK DR   511500   
8464            AUSTIN    TX    78757             6616 ARGENTIA RD  1718376   
3383            AUSTIN    TX    78731      5752 N SCOUT ISLAND CIR   581028   
5466           LAKEWAY    TX    78738         207 COOPERS CROWN LN  1134929   

      bedrooms  bathrooms  square_foot   latitude  longitude  sale_amount  \
4572         4          4         5906  30.262385 -97.875867         3063   
28           4          2         3764  30.461311 -97.847166         1250   
4159         3          2         2126  30.383266 -97.917567        15953   
3477         5          3         4127  30.360082 -97.760467         6250   
6659         3          2         1930  30.187422 -97.792425       367318   
1556         3          2         1729  30.248998 -97.776852        90000   
1763         3          2         2467  30.251778 -97.761709       306438   
5059         4          3         4666  30.287892 -97.941237       375000   
3982         4          3         3396  30.405195 -97.924185       256250   
6978         3          2         2250  30.163786 -97.796674        62500   
8482         3          1         1612  30.350034 -97.732856        62000   
623          3          2         2322  30.468359 -97.984759        39063   
1498         4          4         3665  30.284386 -97.766411        39250   
283          2          2         1322  30.296479 -98.163688       500000   
4474         5          5         4623  30.248501 -97.870925        31250   
2344         2          2         1554  30.297197 -97.700659        12500   
5408         4          4         6908  30.287313 -97.939506       275000   
160          2          1         3062  30.132365 -97.621664        15000   
8436         3          2         2109  30.359103 -97.722873       150000   
4493         5          4   

In [247]:
# Capture visualization for presentation
price_outliers[['sale_transaction_date', 'sale_amount', 'price']].head(5)

sale_transaction_date  sale_amount    price
4572            2023-06-09         3063  4833563
28              2022-02-08         1250   741046
4159            2023-10-02        15953   450080
3477            2021-07-08         6250  1897071
6659            2023-09-15       367318  6754950

In [248]:
# Drop yearly price change outliers
df_outlier = df_outlier.drop(index=price_outliers.index)
df_outlier

city state  zipcode                 address    price  bedrooms  \
0     CEDAR PARK    TX    78613       2704 ORSOBELLO PL   827510         4   
1     CEDAR PARK    TX    78613     2705 QUIET MOON TRL  1064554         5   
2     CEDAR PARK    TX    78613      3204 APPENNINI WAY   956365         4   
3     CEDAR PARK    TX    78613      3125 FIORELLINO PL   776845         4   
4     CEDAR PARK    TX    78613        2316 ALDWORTH DR   945000         6   
...          ...   ...      ...                     ...      ...       ...   
8877      AUSTIN    TX    78758  1401 LORRAINE LOOP # B   485155         2   
8878      AUSTIN    TX    78758     1420A LORRAINE LOOP   449941         2   
8879      AUSTIN    TX    78758      1509 LORRAINE LOOP   541362         3   
8880      AUSTIN    TX    78758     1417 KRAMER LN # 10   701193         3   
8881      AUSTIN    TX    78758      1417 KRAMER LN # 8   701193         3   

      bathrooms  square_foot   latitude  longitude  sale_amount  \
0             3         3715  30.463011 -97.846630       503723   
1             4         5018  30.473855 -97.853806      1100000   
2             3         4145  30.456254 -97.849748       679630   
3             3         3624  30.454730 -97.848842       609375   
4             4         4725  30.467167 -97.851148       781250   
...         ...          ...        ...        ...          ...   
8877          2         1596  30.381360 -97.703334       475000   
8878          2         1596  30.381360 -97.703334       362188   
8879          3         1718  30.381360 -97.703334       540000   
8880          3         2428  30.383131 -97.699892       700000   
8881          3         2428  30.383131 -97.699892       385000   

     sale_transaction_date  years_since_last_sale  yearly_price_change  \
0               2020-01-30               3.854894            16.674591   
1               2022-03-25               1.705681            -1.889195   
2               2020-09-10               3.241615            12.561169   
3               2023-01-04               0.925394            29.697912   
4               2021-12-13               1.984942            10.559503   
...                    ...                    ...                  ...   
8877            2021-08-24               2.288843             0.934050   
8878            2020-06-01               3.518138             6.886761   
8879            2022-05-06               1.590691             0.158561   
8880            2022-04-01               1.686516             0.101054   
8881            2020-10-14               3.148528            26.084583   

      size_bedroom_bathroom_ratio  
0                      530.714286  
1                      557.555556  
2                      592.142857  
3                      517.714286  
4                      472.500000  
...                           ...  
8877                   399.000000  
8878                   399.000000  
8879                   286.333333  
8880                   404.666667  
8881                   404.666667  

[8811 rows x 15 columns]

In [249]:
# Finalize df without the extra columns used for outlier analysis
final_df = df_outlier[['city', 'state', 'zipcode','address', 'price', 'bedrooms','bathrooms','square_foot','latitude','longitude','sale_amount','sale_transaction_date']]
final_df

city state  zipcode                 address    price  bedrooms  \
0     CEDAR PARK    TX    78613       2704 ORSOBELLO PL   827510         4   
1     CEDAR PARK    TX    78613     2705 QUIET MOON TRL  1064554         5   
2     CEDAR PARK    TX    78613      3204 APPENNINI WAY   956365         4   
3     CEDAR PARK    TX    78613      3125 FIORELLINO PL   776845         4   
4     CEDAR PARK    TX    78613        2316 ALDWORTH DR   945000         6   
...          ...   ...      ...                     ...      ...       ...   
8877      AUSTIN    TX    78758  1401 LORRAINE LOOP # B   485155         2   
8878      AUSTIN    TX    78758     1420A LORRAINE LOOP   449941         2   
8879      AUSTIN    TX    78758      1509 LORRAINE LOOP   541362         3   
8880      AUSTIN    TX    78758     1417 KRAMER LN # 10   701193         3   
8881      AUSTIN    TX    78758      1417 KRAMER LN # 8   701193         3   

      bathrooms  square_foot   latitude  longitude  sale_amount  \
0             3         3715  30.463011 -97.846630       503723   
1             4         5018  30.473855 -97.853806      1100000   
2             3         4145  30.456254 -97.849748       679630   
3             3         3624  30.454730 -97.848842       609375   
4             4         4725  30.467167 -97.851148       781250   
...         ...          ...        ...        ...          ...   
8877          2         1596  30.381360 -97.703334       475000   
8878          2         1596  30.381360 -97.703334       362188   
8879          3         1718  30.381360 -97.703334       540000   
8880          3         2428  30.383131 -97.699892       700000   
8881          3         2428  30.383131 -97.699892       385000   

     sale_transaction_date  
0               2020-01-30  
1               2022-03-25  
2               2020-09-10  
3               2023-01-04  
4               2021-12-13  
...                    ...  
8877            2021-08-24  
8878            2020-06-01  
8879            2022-05-06  
8880            2022-04-01  
8881            2020-10-14  

[8811 rows x 12 columns]

In [250]:
final_df = final_df.reset_index(drop=True)
final_df

city state  zipcode                 address    price  bedrooms  \
0     CEDAR PARK    TX    78613       2704 ORSOBELLO PL   827510         4   
1     CEDAR PARK    TX    78613     2705 QUIET MOON TRL  1064554         5   
2     CEDAR PARK    TX    78613      3204 APPENNINI WAY   956365         4   
3     CEDAR PARK    TX    78613      3125 FIORELLINO PL   776845         4   
4     CEDAR PARK    TX    78613        2316 ALDWORTH DR   945000         6   
...          ...   ...      ...                     ...      ...       ...   
8806      AUSTIN    TX    78758  1401 LORRAINE LOOP # B   485155         2   
8807      AUSTIN    TX    78758     1420A LORRAINE LOOP   449941         2   
8808      AUSTIN    TX    78758      1509 LORRAINE LOOP   541362         3   
8809      AUSTIN    TX    78758     1417 KRAMER LN # 10   701193         3   
8810      AUSTIN    TX    78758      1417 KRAMER LN # 8   701193         3   

      bathrooms  square_foot   latitude  longitude  sale_amount  \
0             3         3715  30.463011 -97.846630       503723   
1             4         5018  30.473855 -97.853806      1100000   
2             3         4145  30.456254 -97.849748       679630   
3             3         3624  30.454730 -97.848842       609375   
4             4         4725  30.467167 -97.851148       781250   
...         ...          ...        ...        ...          ...   
8806          2         1596  30.381360 -97.703334       475000   
8807          2         1596  30.381360 -97.703334       362188   
8808          3         1718  30.381360 -97.703334       540000   
8809          3         2428  30.383131 -97.699892       700000   
8810          3         2428  30.383131 -97.699892       385000   

     sale_transaction_date  
0               2020-01-30  
1               2022-03-25  
2               2020-09-10  
3               2023-01-04  
4               2021-12-13  
...                    ...  
8806            2021-08-24  
8807            2020-06-01  
8808            2022-05-06  
8809            2022-04-01  
8810            2020-10-14  

[8811 rows x 12 columns]

In [251]:
final_df.dtypes

city                             object
state                            object
zipcode                           int64
address                          object
price                             int64
bedrooms                          int64
bathrooms                         int64
square_foot                       int64
latitude                        float64
longitude                       float64
sale_amount                       int64
sale_transaction_date    datetime64[ns]
dtype: object

In [252]:
# Save df to CSV
final_df.to_csv('property_df.csv', index=True)